In [1]:
import numpy as np
import matplotlib.pyplot as plt
import h5py
from tensorflow.keras.utils import to_categorical
from sklearn.preprocessing import LabelEncoder

2023-04-09 18:56:25.889806: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-04-09 18:56:25.889828: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


In [2]:
file_str = 'Jan06_FlavFix_smear_1_std_xtd_zst.h5'

In [3]:
f5 = h5py.File(file_str, 'r')
x_train = np.array( f5['x_train'] )
y_train = to_categorical( np.array( f5['y_train'] ) )

n_classes = len(np.unique(y_train, axis=0))

idx = np.random.permutation(len(x_train))
x_train = x_train[idx]
y_train = y_train[idx]

x_test = np.array( f5['x_test'] )
y_test = to_categorical ( np.array( f5['y_test'] ) )

y_train[y_train == -1] = 0
y_test[y_test == -1] = 0

In [4]:
n_classes

3

In [5]:
y_train

array([[1., 0., 0.],
       [0., 0., 1.],
       [0., 0., 1.],
       ...,
       [1., 0., 0.],
       [1., 0., 0.],
       [1., 0., 0.]], dtype=float32)

In [6]:
x_train.shape

(701516, 15, 6)

In [7]:
from tensorflow import keras
from tensorflow.keras import layers

In [8]:
def transformer_encoder(inputs, head_size, num_heads, ff_dim, dropout=0):
    # Normalization and Attention
    x = layers.MultiHeadAttention(
        key_dim=head_size, num_heads=num_heads, dropout=dropout
    )(inputs, inputs)
    x = layers.Dropout(dropout)(x)
    res = layers.Add()([x, inputs])

    # Feed Forward Part
    x = layers.Dense(ff_dim, activation="relu")(res)
    x = layers.Dropout(dropout)(x)
    x = layers.Dense(inputs.shape[-1])(x)
    x = layers.Add()([x, res])
    return x


In [9]:

def build_model(
    input_shape,
    head_size,
    num_heads,
    ff_dim,
    num_transformer_blocks,
    mlp_units,
    dropout=0.15,
    mlp_dropout=0.15,
):
    inputs = keras.Input(shape=input_shape)
    x = inputs
    for _ in range(num_transformer_blocks):
        x = transformer_encoder(x, head_size, num_heads, ff_dim, dropout)

    x = layers.Flatten()(x)
    for dim in mlp_units:
        x = layers.Dense(dim, activation="relu")(x)
        x = layers.Dropout(mlp_dropout)(x)
    outputs = layers.Dense(n_classes, activation="softmax")(x)
    return keras.Model(inputs, outputs)


In [11]:
input_shape = x_train.shape[1:]

model = build_model(
    input_shape,
    head_size=32,
    num_heads=2,
    ff_dim=8,
    num_transformer_blocks=3,
    mlp_units=[32,16,8],
    mlp_dropout=0.15,
    dropout=0.15,
)

# model.compile(
#     loss="sparse_categorical_crossentropy",
#     optimizer=keras.optimizers.Adam(learning_rate=1e-4),
#     metrics=["sparse_categorical_accuracy"],
# )

model.compile(optimizer='adam', loss=['categorical_crossentropy'], metrics=['accuracy'])

model.summary()


Model: "model_1"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_2 (InputLayer)           [(None, 15, 6)]      0           []                               
                                                                                                  
 multi_head_attention_2 (MultiH  (None, 15, 6)       1734        ['input_2[0][0]',                
 eadAttention)                                                    'input_2[0][0]']                
                                                                                                  
 dropout_7 (Dropout)            (None, 15, 6)        0           ['multi_head_attention_2[0][0]'] 
                                                                                                  
 add_4 (Add)                    (None, 15, 6)        0           ['dropout_7[0][0]',        

In [13]:
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint

In [14]:
callbacks = [EarlyStopping(verbose=True, patience=10, monitor='val_accuracy')]

model.fit(
    x_train,
    y_train,
    validation_split=0.2,
    epochs=200,
    batch_size=2**14,
    callbacks=callbacks,
)


Epoch 1/200
35/35 [==============================] - 13s 89ms/step - loss: 1.1126 - accuracy: 0.4234 - val_loss: 1.0042 - val_accuracy: 0.4833
Epoch 2/200
35/35 [==============================] - 3s 83ms/step - loss: 1.0066 - accuracy: 0.4957 - val_loss: 0.9468 - val_accuracy: 0.5819
Epoch 3/200
35/35 [==============================] - 3s 82ms/step - loss: 0.9565 - accuracy: 0.5554 - val_loss: 0.8927 - val_accuracy: 0.6228
Epoch 4/200
35/35 [==============================] - 3s 83ms/step - loss: 0.9116 - accuracy: 0.6016 - val_loss: 0.8503 - val_accuracy: 0.6522
Epoch 5/200
35/35 [==============================] - 3s 83ms/step - loss: 0.8832 - accuracy: 0.6272 - val_loss: 0.8279 - val_accuracy: 0.6615
Epoch 6/200
35/35 [==============================] - 3s 83ms/step - loss: 0.8665 - accuracy: 0.6401 - val_loss: 0.8169 - val_accuracy: 0.6667
Epoch 7/200
35/35 [==============================] - 3s 82ms/step - loss: 0.8543 - accuracy: 0.6486 - val_loss: 0.8079 - val_accuracy: 0.6719
Epoch

35/35 [==============================] - 3s 80ms/step - loss: 0.7253 - accuracy: 0.7174 - val_loss: 0.7073 - val_accuracy: 0.7238
Epoch 116/200
35/35 [==============================] - 3s 85ms/step - loss: 0.7247 - accuracy: 0.7177 - val_loss: 0.7059 - val_accuracy: 0.7236
Epoch 117/200
35/35 [==============================] - 3s 85ms/step - loss: 0.7250 - accuracy: 0.7176 - val_loss: 0.7072 - val_accuracy: 0.7237
Epoch 118/200
35/35 [==============================] - 3s 83ms/step - loss: 0.7256 - accuracy: 0.7171 - val_loss: 0.7089 - val_accuracy: 0.7234
Epoch 119/200
35/35 [==============================] - 3s 80ms/step - loss: 0.7251 - accuracy: 0.7175 - val_loss: 0.7107 - val_accuracy: 0.7229
Epoch 120/200
35/35 [==============================] - 3s 83ms/step - loss: 0.7251 - accuracy: 0.7173 - val_loss: 0.7048 - val_accuracy: 0.7238
Epoch 121/200
35/35 [==============================] - 3s 86ms/step - loss: 0.7251 - accuracy: 0.7176 - val_loss: 0.7062 - val_accuracy: 0.7236
Epoch 

In [15]:
model.evaluate(x_test, y_test, verbose=1)

9396/9396 [==============================] - 25s 3ms/step - loss: 0.7061 - accuracy: 0.7260


[0.7061108350753784, 0.7260435819625854]

## Conclusions



In [16]:
# model.save("b_tag_model.h5")

In [9]:
from tensorflow.keras.models import load_model
model = load_model('b_tag_model.h5')

2023-04-09 18:56:55.111007: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2023-04-09 18:56:55.111579: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-04-09 18:56:55.111653: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcublas.so.11'; dlerror: libcublas.so.11: cannot open shared object file: No such file or directory
2023-04-09 18:56:55.111709: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcublasLt.so.11'; dlerror: libcublasLt.so.11: cannot open shared object file: No such file or directory
2023-04-09 18:56:55.111762: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Co

In [10]:
model.summary()

Model: "model_1"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_2 (InputLayer)           [(None, 15, 6)]      0           []                               
                                                                                                  
 multi_head_attention_2 (MultiH  (None, 15, 6)       1734        ['input_2[0][0]',                
 eadAttention)                                                    'input_2[0][0]']                
                                                                                                  
 dropout_7 (Dropout)            (None, 15, 6)        0           ['multi_head_attention_2[0][0]'] 
                                                                                                  
 add_4 (Add)                    (None, 15, 6)        0           ['dropout_7[0][0]',        

In [1]:
import hls4ml
import os
os.environ['PATH'] = '/opt/Xilinx/Vivado/2019.2/bin:' + os.environ['PATH']

2023-04-14 18:04:24.240576: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-04-14 18:04:24.240591: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
/home/ej/workspace/hls4ml/hls4ml/hls4ml/converters/__init__.py:15: UserWarning: WARNING: Pytorch converter is not enabled!
  warnings.warn("WARNING: Pytorch converter is not enabled!")


In [13]:
config = hls4ml.utils.config_from_keras_model(model, granularity='model', default_precision='ap_fixed<18,8>')
config['Model']['ReuseFactor']=3
config['Model']['Strategy']='Resource'
hls_model = hls4ml.converters.convert_from_keras_model(model,
                                                       hls_config=config,
                                                       output_dir='mha_time_series/hls4ml_prj_reuse3',
                                                       part='xcvu13p-fhga2104-2L-e')

Interpreting Model
Topology:
Layer name: input_2, layer type: Input
Layer name: multi_head_attention_2, layer type: MultiHeadAttention
Layer name: add_4, layer type: Add
Layer name: dense_8, layer type: Dense
  -> Activation (relu), layer name: dense_8
Layer name: dense_9, layer type: Dense
  -> Activation (linear), layer name: dense_9
Layer name: add_5, layer type: Add
Layer name: multi_head_attention_3, layer type: MultiHeadAttention
Layer name: add_6, layer type: Add
Layer name: dense_10, layer type: Dense
  -> Activation (relu), layer name: dense_10
Layer name: dense_11, layer type: Dense
  -> Activation (linear), layer name: dense_11
Layer name: add_7, layer type: Add
Layer name: multi_head_attention_4, layer type: MultiHeadAttention
Layer name: add_8, layer type: Add
Layer name: dense_12, layer type: Dense
  -> Activation (relu), layer name: dense_12
Layer name: dense_13, layer type: Dense
  -> Activation (linear), layer name: dense_13
Layer name: add_9, layer type: Add
Layer nam

In [14]:
hls_model.compile()

Writing HLS project
Done


In [15]:
x_test1=np.ascontiguousarray(x_test[5:15,:,:])

In [15]:
hls_model.build(csim=True, synth=True, vsynth=True)


****** Vivado(TM) HLS - High-Level Synthesis from C, C++ and SystemC v2019.2 (64-bit)
  **** SW Build 2708876 on Wed Nov  6 21:39:14 MST 2019
  **** IP Build 2700528 on Thu Nov  7 00:09:20 MST 2019
    ** Copyright 1986-2019 Xilinx, Inc. All Rights Reserved.

source /opt/Xilinx/Vivado/2019.2/scripts/vivado_hls/hls.tcl -notrace
INFO: [HLS 200-10] Running '/opt/Xilinx/Vivado/2019.2/bin/unwrapped/lnx64.o/vivado_hls'
INFO: [HLS 200-10] For user 'ej' on host 'ej-ubt' (Linux_x86_64 version 5.4.0-146-generic) on Sun Apr 09 18:57:16 PDT 2023
INFO: [HLS 200-10] On os Ubuntu 18.04.6 LTS
INFO: [HLS 200-10] In directory '/home/ej/workspace/B_tagging_transformer/mha_time_series/hls4ml_prj_reuse2_v3'
Sourcing Tcl script 'build_prj.tcl'
INFO: [HLS 200-10] Creating and opening project '/home/ej/workspace/B_tagging_transformer/mha_time_series/hls4ml_prj_reuse2_v3/myproject_prj'.
INFO: [HLS 200-10] Adding design file 'firmware/myproject.cpp' to the project
INFO: [HLS 200-10] Adding test bench file 'myp

INFO: [HLS 200-111] Finished Linking Time (s): cpu = 00:00:21 ; elapsed = 00:00:31 . Memory (MB): peak = 893.523 ; gain = 459.035 ; free physical = 18862 ; free virtual = 35437
INFO: [HLS 200-111] Finished Checking Pragmas Time (s): cpu = 00:00:21 ; elapsed = 00:00:31 . Memory (MB): peak = 893.523 ; gain = 459.035 ; free physical = 18862 ; free virtual = 35437
INFO: [HLS 200-10] Starting code transformations ...
INFO: [XFORM 203-603] Inlining function 'nnet::product::mult<ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0>, ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0> >::limit' into 'nnet::dense_latency<ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0>, ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0>, config2_1>' (firmware/nnet_utils/nnet_dense_latency.h:56).
INFO: [XFORM 203-603] Inlining function 'nnet::product::mult<ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0>, ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0> >::limit' into 'nnet::dense_latency<ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0

INFO: [HLS 200-111] Finished Standard Transforms Time (s): cpu = 00:00:30 ; elapsed = 00:00:40 . Memory (MB): peak = 963.250 ; gain = 528.762 ; free physical = 18701 ; free virtual = 35302
INFO: [HLS 200-10] Checking synthesizability ...
INFO: [XFORM 203-602] Inlining function 'fp_struct<double>::mantissa' into 'generic_cast_IEEE754<int, (ap_q_mode)6, double>' (/wrk/2019.2/continuous/2019_11_06_2708876/src/products/hls/hls_lib/hlsmath/include/FloatingPoint/hls_case_IEEE754.h:15) automatically.
INFO: [XFORM 203-602] Inlining function 'fp_struct<double>::expv' into 'generic_cast_IEEE754<int, (ap_q_mode)6, double>' (/wrk/2019.2/continuous/2019_11_06_2708876/src/products/hls/hls_lib/hlsmath/include/FloatingPoint/hls_case_IEEE754.h:18) automatically.
INFO: [XFORM 203-602] Inlining function 'fp_struct<double>::__signbit' into 'generic_cast_IEEE754<int, (ap_q_mode)6, double>' (/wrk/2019.2/continuous/2019_11_06_2708876/src/products/hls/hls_lib/hlsmath/include/FloatingPoint/hls_case_IEEE754.h:5

INFO: [HLS 200-111] Finished Checking Synthesizability Time (s): cpu = 00:00:41 ; elapsed = 00:00:51 . Memory (MB): peak = 963.250 ; gain = 528.762 ; free physical = 18694 ; free virtual = 35290
INFO: [XFORM 203-1101] Packing variable 'v_proj.V.data.V' (firmware/nnet_utils/nnet_multiheadattention.h:292) into a 576-bit variable.
INFO: [XFORM 203-1101] Packing variable 'datav_pack.data.V' (firmware/nnet_utils/nnet_multiheadattention.h:130) into a 576-bit variable.
INFO: [XFORM 203-1101] Packing variable 'q_proj.V.data.V' (firmware/nnet_utils/nnet_multiheadattention.h:290) into a 576-bit variable.
INFO: [XFORM 203-1101] Packing variable 'k_proj.V.data.V' (firmware/nnet_utils/nnet_multiheadattention.h:291) into a 576-bit variable.
INFO: [XFORM 203-1101] Packing variable 'datak_pack.data.V' (firmware/nnet_utils/nnet_multiheadattention.h:75) into a 576-bit variable.
INFO: [XFORM 203-1101] Packing variable 'dataq_pack.data.V' (firmware/nnet_utils/nnet_multiheadattention.h:75) into a 576-bit v

INFO: [HLS 200-489] Unrolling loop 'qk' (firmware/nnet_utils/nnet_multiheadattention.h:154) in function 'nnet::matrixmul<ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0>, ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0>, config16>' completely with a factor of 15.
INFO: [HLS 200-489] Unrolling loop 'col' (firmware/nnet_utils/nnet_multiheadattention.h:158) in function 'nnet::matrixmul<ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0>, ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0>, config16>' completely with a factor of 32.
INFO: [HLS 200-489] Unrolling loop 'product' (firmware/nnet_utils/nnet_multiheadattention.h:161) in function 'nnet::matrixmul<ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0>, ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0>, config16>' completely with a factor of 15.
INFO: [HLS 200-489] Unrolling loop 'Loop-1.1' (firmware/nnet_utils/nnet_multiheadattention.h:39) in function 'nnet::matrixmul_transpose<ap_fixed<18, 8, (ap_q_mode)5, (ap_o_mode)3, 0>, ap_fixed<18, 8, (ap_q_mode)5, 

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



|9054  |    U_fifo_w18_d2_A_x1_ram                                                         |fifo_w18_d2_A_x1_shiftReg_4925                                                                                                                                                                                                                                            |      55|
|9055  |  layer9_out_12_V_U                                                                |fifo_w18_d2_A_x1_2275                                                                                                                                                                                                                                                     |      66|
|9056  |    U_fifo_w18_d2_A_x1_ram                                                         |fifo_w18_d2_A_x1_shiftReg_4923                                                                                                                                            

Synthesis Optimization Runtime : Time (s): cpu = 00:34:04 ; elapsed = 00:39:38 . Memory (MB): peak = 13831.945 ; gain = 12351.438 ; free physical = 11087 ; free virtual = 18358
Synthesis Optimization Complete : Time (s): cpu = 00:34:04 ; elapsed = 00:39:38 . Memory (MB): peak = 13831.945 ; gain = 12351.438 ; free physical = 11249 ; free virtual = 18363
INFO: [Project 1-571] Translating synthesized netlist
Netlist sorting complete. Time (s): cpu = 00:00:06 ; elapsed = 00:00:06 . Memory (MB): peak = 13831.945 ; gain = 0.000 ; free physical = 10328 ; free virtual = 17452
INFO: [Netlist 29-17] Analyzing 31592 Unisim elements for replacement
INFO: [Netlist 29-28] Unisim Transformation completed in 23 CPU seconds
INFO: [Project 1-570] Preparing netlist for logic optimization
INFO: [Opt 31-138] Pushed 0 inverter(s) to 0 load pin(s).
INFO: [Opt 31-422] The CLOCK_DOMAINS attribute on the BRAM cell multiheadattention_ap_fixed_ap_fixed_config16_U0/matrixmul_transpose_ap_fixed_ap_fixed_config16_66

Netlist sorting complete. Time (s): cpu = 00:00:00.14 ; elapsed = 00:00:00.14 . Memory (MB): peak = 13876.047 ; gain = 0.000 ; free physical = 8927 ; free virtual = 16092
INFO: [Project 1-111] Unisim Transformation Summary:
  A total of 6885 instances were transformed.
  BUFG => BUFGCE: 1 instance 
  DSP48E2 => DSP48E2 (DSP_ALU, DSP_A_B_DATA, DSP_C_DATA, DSP_MULTIPLIER, DSP_M_DATA, DSP_OUTPUT, DSP_PREADD, DSP_PREADD_DATA): 5080 instances
  IBUF => IBUF (IBUFCTRL, INBUF): 1624 instances
  RAM32M16 => RAM32M16 (RAMD32(x14), RAMS32(x2)): 180 instances

INFO: [Common 17-83] Releasing license: Synthesis
1070 Infos, 215 Warnings, 0 Critical Warnings and 0 Errors encountered.
synth_design completed successfully
synth_design: Time (s): cpu = 00:36:16 ; elapsed = 00:42:00 . Memory (MB): peak = 13876.047 ; gain = 12428.359 ; free physical = 10198 ; free virtual = 17361
# report_utilization -file vivado_synth.rpt
INFO: [Common 17-206] Exiting Vivado at Mon Apr 10 03:40:07 2023...
***** VIVADO SYN

{'CSimResults': [['0.677734', '0.160156', '0.163086']],
 'CSynthesisReport': {'EstimatedClockPeriod': '7.913',
  'BestLatency': '673',
  'WorstLatency': '673',
  'IntervalMin': '99',
  'IntervalMax': '99',
  'BRAM_18K': '1780',
  'DSP48E': '5082',
  'FF': '533662',
  'LUT': '817844',
  'URAM': '0',
  'AvailableBRAM_18K': '5376',
  'AvailableDSP48E': '12288',
  'AvailableFF': '3456000',
  'AvailableLUT': '1728000',
  'AvailableURAM': '1280'},
 'VivadoSynthReport': {'LUT': '342721',
  'FF': '577878',
  'BRAM_18K': '306.5',
  'URAM': '0',
  'DSP48E': '5080'}}

In [2]:
hls4ml.report.read_vivado_report('mha_time_series/hls4ml_prj_reuse3')

Found 1 solution(s) in mha_time_series/hls4ml_prj_reuse3/myproject_prj.
Reports for solution "solution1":

C SIMULATION RESULT:
INFO: [SIM 2] *************** CSIM start ***************
INFO: [SIM 4] CSIM will launch GCC as the compiler.
   Compiling ../../../../myproject_test.cpp in debug mode
   Compiling ../../../../firmware/myproject.cpp in debug mode
   Generating csim.exe
INFO: Unable to open input/predictions file, using default input.
0.677734 0.160156 0.163086 
INFO: Saved inference results to file: tb_data/csim_results.log
INFO: [SIM 1] CSim done with 0 errors.
INFO: [SIM 3] *************** CSIM finish ***************

SYNTHESIS REPORT:
== Vivado HLS Report for 'myproject'
* Date:           Mon Apr 10 02:50:02 2023

* Version:        2019.2 (Build 2704478 on Wed Nov 06 22:10:23 MST 2019)
* Project:        myproject_prj
* Solution:       solution1
* Product family: virtexuplus
* Target device:  xcvu13p-fhga2104-2L-e


== Performance Estimates
+ Timing: 
    * Summary: 
    +---